In [48]:
import folium
import matplotlib.pyplot as plt

from collections import defaultdict
from pyasn import pyasn
from math import pi, cos
from dataclasses import dataclass
from loguru import logger

from geogiant.common.utils import EvalResults, get_parsed_vps
from geogiant.common.queries import load_vps
from geogiant.common.files_utils import load_pickle, load_csv
from geogiant.common.ip_addresses_utils import get_prefix_from_ip
from geogiant.common.settings import PathSettings, ClickhouseSettings

path_settings = PathSettings()
clickhouse_settings = ClickhouseSettings()

asndb = pyasn(str(path_settings.RIB_TABLE))
vps = load_vps(clickhouse_settings.VPS_FILTERED)
vps_per_subnet, vps_coordinates = get_parsed_vps(vps, asndb)


@dataclass(frozen=True)
class ResultsScore:
    client_granularity: str
    answer_granularity: str
    scores: list
    inconsistent_mappings: list


def plotDot(lat, lon, map, color="blue", radius: int = 2):
    """input: series that contains a numeric named latitude and a numeric named longitude
    this function creates a CircleMarker and adds it to your this_map"""
    folium.CircleMarker(
        location=[lat, lon],
        radius=radius,
        weight=radius,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=1,
    ).add_to(map)

2024-05-06 14:15:35.844 | INFO     | geogiant.clickhouse.query:execute:122 - query=GetVPs table_name=filtered_vps  limit=None


# Geoloc map

In [49]:
ref_shortest_ping_results = load_pickle(
    path_settings.RESULTS_PATH / "results_ref_shortest_ping.pickle"
)


eval: EvalResults = load_pickle(
    path_settings.RESULTS_PATH
    / "tier4_evaluation/results__best_hostname_geo_score_20_BGP_3_hostnames_per_org_ns.pickle"
)

In [52]:
granularity = "answer_bgp_prefix"
results_answer_subnet = eval.results_answer_subnets

count = 0
costs = []

d_error_per_budget = defaultdict(dict)
for target, target_results in results_answer_subnet.items():
    try:
        ecs_shortest_ping_vp = target_results["result_per_metric"]["jaccard"][
            "ecs_shortest_ping_vp_per_budget"
        ][50]
        no_ping_vp = target_results["result_per_metric"]["jaccard"]["no_ping_vp"]

    except KeyError:
        continue

    ecs_shortest_ping_vps = target_results["result_per_metric"]["jaccard"]["ecs_vps"]

    d_error = ecs_shortest_ping_vp["d_error"]

    target = target_results["target"]

    try:
        ref_shortest_ping_vp = ref_shortest_ping_results[target["addr"]][
            "ref_shortest_ping_vp"
        ]
    except:
        continue

    diff_error = ref_shortest_ping_vp["d_error"] - d_error

    if diff_error < 50:

        if target["addr"] != "5.180.228.37":
            continue

        count += 1
        if count > 100:
            break

        logger.info("Target::")
        logger.info(f"{target['addr']=}")
        logger.info(f"{target['subnet']=}")
        logger.info(f"{target['lat']=}")
        logger.info(f"{target['lon']=}")

        logger.info("ECS shortest ping vp::")
        logger.info(f"{ecs_shortest_ping_vp['addr']=}")
        logger.info(f"{ecs_shortest_ping_vp['subnet']=}")
        logger.info(f"{ecs_shortest_ping_vp['lat']=}")
        logger.info(f"{ecs_shortest_ping_vp['lon']=}")
        logger.info(f"{ecs_shortest_ping_vp['rtt']=}")
        logger.info(f"{ecs_shortest_ping_vp['d_error']=}")
        logger.info(f"{ecs_shortest_ping_vp['score']=}")

        # logger.info("No ping vp::")
        # logger.info(f"{no_ping_vp['addr']=}")
        # logger.info(f"{no_ping_vp['subnet']=}")
        # logger.info(f"{no_ping_vp['lat']=}")
        # logger.info(f"{no_ping_vp['lon']=}")
        # logger.info(f"{no_ping_vp['d_error']=}")
        # logger.info(f"{no_ping_vp['score']=}")

        # logger.info("REF shortest ping vp::")
        # logger.info(f"{ref_shortest_ping_vp['addr']=}")
        # logger.info(f"{ref_shortest_ping_vp['subnet']=}")
        # logger.info(f"{ref_shortest_ping_vp['lat']=}")
        # logger.info(f"{ref_shortest_ping_vp['lon']=}")
        # logger.info(f"{ref_shortest_ping_vp['rtt']=}")
        # logger.info(f"{ref_shortest_ping_vp['d_error']=}")

        count += 1

        # if count > 10:
        #     break

        r_earth = 6378
        d = d_error
        new_latitude = target["lat"] + (d / r_earth) * (180 / pi)
        new_longitude = target["lon"] + (d / r_earth) * (180 / pi) / cos(
            target["lat"] * pi / 180
        )

        min_lat = target["lat"] - (d / r_earth) * (180 / pi)
        max_lat = target["lat"] + (d / r_earth) * (180 / pi)
        min_lon = target["lon"] - (d / r_earth) * (180 / pi) / cos(
            target["lat"] * pi / 180
        )
        max_lon = target["lon"] + (d / r_earth) * (180 / pi) / cos(
            target["lat"] * pi / 180
        )

        map = folium.Map(
            location=(target["lat"], target["lon"]),
            zoom_start=6,
            min_lat=min_lat,
            max_lat=max_lat,
            min_lon=min_lon,
            max_lon=max_lon,
        )

        for vp in vps:
            try:
                vp_lat, vp_lon, _ = vps_coordinates[vp["addr"]]
                plotDot(vp_lat, vp_lon, map, color="grey")
                ping_done += 1
            except KeyError as e:
                print(e)
                continue

        ping_done = 0
        for vp_addr, _ in ecs_shortest_ping_vps:
            try:
                vp_lat, vp_lon, _ = vps_coordinates[vp_addr]
                plotDot(vp_lat, vp_lon, map, color="cyan", radius=4)
                ping_done += 1
            except KeyError as e:
                print(e)
                continue

        logger.info(f"True number of VP selected: {ping_done}")

        # selected_vp_coordinates = np.array(selected_vp_coordinates, dtype=float)

        plotDot(target["lat"], target["lon"], map, color="red", radius=6)
        # plotDot(
        #     ecs_shortest_ping_vp["lat"], ecs_shortest_ping_vp["lon"], map, color="blue"
        # )

        # plotDot(no_ping_vp["lat"], no_ping_vp["lon"], map, color="pink")
        # plotDot(
        #     ref_shortest_ping_vp["lat"], ref_shortest_ping_vp["lon"], map, color="green"
        # )
        # plotDot(cluster_elected_lat, cluster_elected_lon, map, color="orange")

        display(map)

logger.info(f"Nb wrongful geoloc:: {count}")

2024-05-06 14:16:16.809 | INFO     | __main__:<module>:42 - Target::
2024-05-06 14:16:16.810 | INFO     | __main__:<module>:43 - target['addr']='5.180.228.37'
2024-05-06 14:16:16.812 | INFO     | __main__:<module>:44 - target['subnet']='5.180.228.0'
2024-05-06 14:16:16.813 | INFO     | __main__:<module>:45 - target['lat']=40.4415
2024-05-06 14:16:16.814 | INFO     | __main__:<module>:46 - target['lon']=-3.6185
2024-05-06 14:16:16.815 | INFO     | __main__:<module>:48 - ECS shortest ping vp::
2024-05-06 14:16:16.816 | INFO     | __main__:<module>:49 - ecs_shortest_ping_vp['addr']='185.161.96.30'
2024-05-06 14:16:16.817 | INFO     | __main__:<module>:50 - ecs_shortest_ping_vp['subnet']='185.161.96.0'
2024-05-06 14:16:16.818 | INFO     | __main__:<module>:51 - ecs_shortest_ping_vp['lat']=40.4175
2024-05-06 14:16:16.818 | INFO     | __main__:<module>:52 - ecs_shortest_ping_vp['lon']=-3.6925
2024-05-06 14:16:16.821 | INFO     | __main__:<module>:53 - ecs_shortest_ping_vp['rtt']=0.341132
202

2024-05-06 14:16:17.235 | INFO     | __main__:<module>:122 - True number of VP selected: 50


2024-05-06 14:16:24.303 | INFO     | __main__:<module>:139 - Nb wrongful geoloc:: 2


# ALL hostnames analysis